# Library imports

In [18]:
from scipy.stats import percentileofscore as score
from scipy import stats
import pandas as pd
import numpy as np 
import xlsxwriter 
import requests
import math

# Importing Our List of Stocks and getting API Token


In [19]:
pd.set_option('display.max_rows', None)
stocks = pd.read_csv('sp_500_stocks.csv')
IEX_CLOUD_API_TOKEN = 'Tpk_059b97af715d417d9f49f50b51b1c448'
symbol = 'AAPL'
api_url = f'https://sandbox.iexapis.com/stable/stock/{symbol}/stats/?token={IEX_CLOUD_API_TOKEN}'
data = requests.get(api_url).json()
data

{'companyName': 'Apple Inc',
 'marketcap': 2370000253296,
 'week52high': 190.5,
 'week52low': 134.45,
 'week52highSplitAdjustOnly': 186.81,
 'week52lowSplitAdjustOnly': 133.22,
 'week52change': -0.18501761482322374,
 'sharesOutstanding': 16040609789,
 'float': 0,
 'avg10Volume': 73833533,
 'avg30Volume': 75890581,
 'day200MovingAvg': 156,
 'day50MovingAvg': 150.71,
 'employees': 151281,
 'ttmEPS': 6.18,
 'ttmDividendRate': 0.9379619150608087,
 'dividendYield': 0.006378359578878771,
 'nextDividendDate': '',
 'exDividendDate': '2022-10-23',
 'nextEarningsDate': '2023-01-17',
 'peRatio': 23.07493451125092,
 'beta': 1.3335872966655795,
 'maxChangePercent': 55.58902986946302,
 'year5ChangePercent': 2.59614235934996,
 'year2ChangePercent': 0.16699685267337164,
 'year1ChangePercent': -0.180740529512582,
 'ytdChangePercent': -0.1932025913216303,
 'month6ChangePercent': -0.034041517537914484,
 'month3ChangePercent': -0.07520461343837648,
 'month1ChangePercent': 0.02265941821125522,
 'day30Chang

# Executing a batch API Call & Building our Dataframe

In this section, we will filter for stocks with the lowest percentiles on the following metrics:

    1. Price-to-earnings ratio (Equivalent in portuguese: P/L - Preço sobre lucro)
    2. Price-to-book ratio (Equivalent in portuguese: P/VP - Preço sobre Valor Patrimonial)
    3. Price-to-sales ratio (Equivalent in portuguese: P/S - Preço sobre vendas
    4. Enterprise Value divided by earnings before interest, taxes, depreciation, and amortization (EV/EBITDA)
    5. Enterprise Value divided by gross profit (EV/GP)

Some of these metrics aren't provided directly by the IEX Cloud API, and must be computed after pulling raw data.

In [20]:
rv_columns = [
    'Ticker',
    'companyName',
    'Price',
    'Number of Shares to Buy',
    'Price-to-Earnings Ratio',
    'PE Percentile',
    'Price-to-Book Ratio',
    'PB Percentile',
    'Price-to-Sales Ratio',
    'PS Percentile',
    'EV/EBITDA',
    'EV/EBITDA Percentile',
    'EV/GP',
    'EV/GP Percentile',
    'RV Score',
    'Aumento de preco 1 ANO',
    'Aumento de preco 2 ANOS',
    'Aumento de preco 5 ANOS',
    'dividend yield'
]

rv_dataframe = pd.DataFrame(columns = rv_columns)
rv_dataframe

Empty DataFrame
Columns: [Ticker, companyName, Price, Number of Shares to Buy, Price-to-Earnings Ratio, PE Percentile, Price-to-Book Ratio, PB Percentile, Price-to-Sales Ratio, PS Percentile, EV/EBITDA, EV/EBITDA Percentile, EV/GP, EV/GP Percentile, RV Score, Aumento de preco 1 ANO, Aumento de preco 2 ANOS, Aumento de preco 5 ANOS, dividend yield]
Index: []

In [30]:
def chunks(lst,n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i : i + n]

symbol_groups = list(chunks(stocks['Ticker'],100))
symbol_strings = []
for i in range(0, len(symbol_groups)):
    
    symbol_strings.append(','.join(symbol_groups[i]))
    #print (symbol_strings[i])
    
    
for symbol_string in symbol_strings[:6]:      
    batch_api_call_url = f'https://sandbox.iexapis.com/stable/stock/market/batch?symbols={symbol_string} &types=quote,price,stats,advanced-stats&token={IEX_CLOUD_API_TOKEN}'
    data = requests.get(batch_api_call_url).json()
    
    for symbol in symbol_string.split(','):
        
        
        enterprise_value = data[symbol]['advanced-stats']['enterpriseValue']
        ebitda = data[symbol]['advanced-stats']['EBITDA']

        # Enterprise value divided by Gross Profit (EV/GP)
        gross_profit = data[symbol]['advanced-stats']['grossProfit']
        
        try:
            ev_to_gross_profit = enterprise_value/gross_profit
        except:
            ev_to_gross_profit = np.NaN
        
        
        try:
            ev_to_ebitda = enterprise_value/ebitda
        except TypeError:
            ev_to_ebitda = np.NaN
        
        rv_dataframe = rv_dataframe.append(
            pd.Series([
                symbol,
                data[symbol]['quote']['companyName'],
                data[symbol]['quote']['latestPrice'],
                'N/A',
                data[symbol]['quote']['peRatio'],
                'N/A',
                data[symbol]['advanced-stats']['priceToBook'],
                'N/A',
                data[symbol]['advanced-stats']['priceToSales'],
                'N/A',
                ev_to_ebitda,
                'N/A',
                ev_to_gross_profit,
                'N/A',            
                'N/A',
                data[symbol]['stats']['year1ChangePercent'],
                data[symbol]['stats']['year2ChangePercent'],
                data[symbol]['stats']['year5ChangePercent'],
                data[symbol]['stats']['dividendYield']
        ],
        index = rv_columns), ignore_index = True)
        
rv_dataframe
     

Ticker                                        companyName     Price  \
0      AAP                             Advance Auto Parts Inc   150.190   
1     AAPL                                          Apple Inc   147.280   
2     ABBV                                         Abbvie Inc   169.430   
3      ABC                           Amerisource Bergen Corp.   167.850   
4     ABMD                                       Abiomed Inc.   392.950   
5      ABT                                Abbott Laboratories   110.250   
6      ACN                            Accenture plc - Class A   300.435   
7     ADBE                                          Adobe Inc   337.970   
8      ADI                                Analog Devices Inc.   175.700   
9      ADM                         Archer Daniels Midland Co.    97.400   
10     ADP                     Automatic Data Processing Inc.   271.375   
11    ADSK                                      Autodesk Inc.   202.750   
12     AEE                                       Ameren Corp.    90.980   
13     AEP               American Electric Power Company Inc.   101.900   
14     AES                                          AES Corp.    30.040   
15     AFL                                         Aflac Inc.    70.090   
16     AIG                   American International Group Inc    64.050   
17     AIV    Apartment Investment & Management Co. - Class A     8.448   
18     AIZ                                       Assurant Inc   132.520   
19     AJG                          Arthur J. Gallagher & Co.   200.616   
20    AKAM                            Akamai Technologies Inc    92.770   
21     ALB                                    Albemarle Corp.   259.984   
22    ALGN                             Align Technology, Inc.   193.100   
23     ALK                              Alaska Air Group Inc.    46.020   
24     ALL                                Allstate Corp (The)   135.660   
25    ALLE                                       Allegion plc   111.850   
26    ALXN                       Alexion Pharmaceuticals Inc.   187.800   
27    AMAT                             Applied Materials Inc.   114.480   
28    AMCR                                          Amcor Plc    13.130   
29     AMD                        Advanced Micro Devices Inc.    73.230   
30     AME                                         Ametek Inc   142.848   
31    AMGN                                         AMGEN Inc.   290.665   
32     AMP                           Ameriprise Financial Inc   324.307   
33     AMT                               American Tower Corp.   216.865   
34    AMZN                                    Amazon.com Inc.    92.440   
35    ANET                                Arista Networks Inc   133.180   
36    ANSS                     Ansys Inc. - Registered Shares   254.330   
37    ANTM                                         Anthem Inc   497.530   
38     AON                                 Aon plc. - Class A   321.883   
39     AOS                                   A.O. Smith Corp.    60.820   
40     APA                                    APA Corporation    43.560   
41     APD                      Air Products & Chemicals Inc.   321.841   
42     APH                           Amphenol Corp. - Class A    82.150   
43    APTV                                          Aptiv PLC    93.120   
44     ARE               Alexandria Real Estate Equities Inc.   152.210   
45     ATO                                 Atmos Energy Corp.   122.360   
46    ATVI                            Activision Blizzard Inc    76.009   
47     AVB                         Avalonbay Communities Inc.   172.180   
48    AVGO                                       Broadcom Inc   550.100   
49     AVY                               Avery Dennison Corp.   180.800   
50     AWK                      American Water Works Co. Inc.   157.547   
51     AXP                               American Express Co.   158.860   
52     AZO                   

# Dealing with Missing Data in Our DataFrame
Our DataFrame contains some missing data because all of the metrics we require are not available through the API we're using.

You can use pandas' isnull method to identify missing data.

In [31]:
rv_dataframe[rv_dataframe.isnull().any(axis=1)].index

Int64Index([115, 161, 321, 322, 524, 536, 567, 613, 616, 630, 659, 680, 684,
            687, 698, 747, 818, 819, 820, 841, 853, 935, 945, 986],
           dtype='int64')

Dealing with missing data is an important topic in data science.

There are 2 main approaches:

1. Drop missing data from the data set (pandas's dropna method is useful here)
2. Replace missing data with a new value (pandas' fillna method is useful here)

In [34]:
rv_dataframe_filled = rv_dataframe
for column in ['Price-to-Earnings Ratio', 'Price-to-Book Ratio', 'Price-to-Sales Ratio', 'EV/EBITDA', 'EV/GP', 'Aumento de preco 1 ANO', 'Aumento de preco 2 ANOS', 'Aumento de preco 5 ANOS']:
    rv_dataframe_filled[column].fillna(rv_dataframe[column].mean(), inplace = True)
rv_dataframe_filled

Ticker                                        companyName     Price  \
0      AAP                             Advance Auto Parts Inc   150.190   
1     AAPL                                          Apple Inc   147.280   
2     ABBV                                         Abbvie Inc   169.430   
3      ABC                           Amerisource Bergen Corp.   167.850   
4     ABMD                                       Abiomed Inc.   392.950   
5      ABT                                Abbott Laboratories   110.250   
6      ACN                            Accenture plc - Class A   300.435   
7     ADBE                                          Adobe Inc   337.970   
8      ADI                                Analog Devices Inc.   175.700   
9      ADM                         Archer Daniels Midland Co.    97.400   
10     ADP                     Automatic Data Processing Inc.   271.375   
11    ADSK                                      Autodesk Inc.   202.750   
12     AEE                                       Ameren Corp.    90.980   
13     AEP               American Electric Power Company Inc.   101.900   
14     AES                                          AES Corp.    30.040   
15     AFL                                         Aflac Inc.    70.090   
16     AIG                   American International Group Inc    64.050   
17     AIV    Apartment Investment & Management Co. - Class A     8.448   
18     AIZ                                       Assurant Inc   132.520   
19     AJG                          Arthur J. Gallagher & Co.   200.616   
20    AKAM                            Akamai Technologies Inc    92.770   
21     ALB                                    Albemarle Corp.   259.984   
22    ALGN                             Align Technology, Inc.   193.100   
23     ALK                              Alaska Air Group Inc.    46.020   
24     ALL                                Allstate Corp (The)   135.660   
25    ALLE                                       Allegion plc   111.850   
26    ALXN                       Alexion Pharmaceuticals Inc.   187.800   
27    AMAT                             Applied Materials Inc.   114.480   
28    AMCR                                          Amcor Plc    13.130   
29     AMD                        Advanced Micro Devices Inc.    73.230   
30     AME                                         Ametek Inc   142.848   
31    AMGN                                         AMGEN Inc.   290.665   
32     AMP                           Ameriprise Financial Inc   324.307   
33     AMT                               American Tower Corp.   216.865   
34    AMZN                                    Amazon.com Inc.    92.440   
35    ANET                                Arista Networks Inc   133.180   
36    ANSS                     Ansys Inc. - Registered Shares   254.330   
37    ANTM                                         Anthem Inc   497.530   
38     AON                                 Aon plc. - Class A   321.883   
39     AOS                                   A.O. Smith Corp.    60.820   
40     APA                                    APA Corporation    43.560   
41     APD                      Air Products & Chemicals Inc.   321.841   
42     APH                           Amphenol Corp. - Class A    82.150   
43    APTV                                          Aptiv PLC    93.120   
44     ARE               Alexandria Real Estate Equities Inc.   152.210   
45     ATO                                 Atmos Energy Corp.   122.360   
46    ATVI                            Activision Blizzard Inc    76.009   
47     AVB                         Avalonbay Communities Inc.   172.180   
48    AVGO                                       Broadcom Inc   550.100   
49     AVY                               Avery Dennison Corp.   180.800   
50     AWK                      American Water Works Co. Inc.   157.547   
51     AXP                               American Express Co.   158.860   
52     AZO                   

Now, if we run the statement from earlier to print rows that contain missing data, nothing should be returned:

In [35]:
rv_dataframe_filled[rv_dataframe_filled.isnull().any(axis=1)]
rv_dataframe_filled


Ticker                                        companyName     Price  \
0      AAP                             Advance Auto Parts Inc   150.190   
1     AAPL                                          Apple Inc   147.280   
2     ABBV                                         Abbvie Inc   169.430   
3      ABC                           Amerisource Bergen Corp.   167.850   
4     ABMD                                       Abiomed Inc.   392.950   
5      ABT                                Abbott Laboratories   110.250   
6      ACN                            Accenture plc - Class A   300.435   
7     ADBE                                          Adobe Inc   337.970   
8      ADI                                Analog Devices Inc.   175.700   
9      ADM                         Archer Daniels Midland Co.    97.400   
10     ADP                     Automatic Data Processing Inc.   271.375   
11    ADSK                                      Autodesk Inc.   202.750   
12     AEE                                       Ameren Corp.    90.980   
13     AEP               American Electric Power Company Inc.   101.900   
14     AES                                          AES Corp.    30.040   
15     AFL                                         Aflac Inc.    70.090   
16     AIG                   American International Group Inc    64.050   
17     AIV    Apartment Investment & Management Co. - Class A     8.448   
18     AIZ                                       Assurant Inc   132.520   
19     AJG                          Arthur J. Gallagher & Co.   200.616   
20    AKAM                            Akamai Technologies Inc    92.770   
21     ALB                                    Albemarle Corp.   259.984   
22    ALGN                             Align Technology, Inc.   193.100   
23     ALK                              Alaska Air Group Inc.    46.020   
24     ALL                                Allstate Corp (The)   135.660   
25    ALLE                                       Allegion plc   111.850   
26    ALXN                       Alexion Pharmaceuticals Inc.   187.800   
27    AMAT                             Applied Materials Inc.   114.480   
28    AMCR                                          Amcor Plc    13.130   
29     AMD                        Advanced Micro Devices Inc.    73.230   
30     AME                                         Ametek Inc   142.848   
31    AMGN                                         AMGEN Inc.   290.665   
32     AMP                           Ameriprise Financial Inc   324.307   
33     AMT                               American Tower Corp.   216.865   
34    AMZN                                    Amazon.com Inc.    92.440   
35    ANET                                Arista Networks Inc   133.180   
36    ANSS                     Ansys Inc. - Registered Shares   254.330   
37    ANTM                                         Anthem Inc   497.530   
38     AON                                 Aon plc. - Class A   321.883   
39     AOS                                   A.O. Smith Corp.    60.820   
40     APA                                    APA Corporation    43.560   
41     APD                      Air Products & Chemicals Inc.   321.841   
42     APH                           Amphenol Corp. - Class A    82.150   
43    APTV                                          Aptiv PLC    93.120   
44     ARE               Alexandria Real Estate Equities Inc.   152.210   
45     ATO                                 Atmos Energy Corp.   122.360   
46    ATVI                            Activision Blizzard Inc    76.009   
47     AVB                         Avalonbay Communities Inc.   172.180   
48    AVGO                                       Broadcom Inc   550.100   
49     AVY                               Avery Dennison Corp.   180.800   
50     AWK                      American Water Works Co. Inc.   157.547   
51     AXP                               American Express Co.   158.860   
52     AZO                   

# Dealing with Price-to-Earnings Ratio < 0

An negative PeRatio indicates that the company has a negative profit, it means, a loss. 
In this approach, I'll remove companies that had a loss.

In [36]:
for row in rv_dataframe_filled.index:
    if (rv_dataframe_filled.loc[row,'Price-to-Earnings Ratio'] < 0):
        rv_dataframe_filled.drop(row)      
                
rv_dataframe_filled

Ticker                                        companyName     Price  \
0      AAP                             Advance Auto Parts Inc   150.190   
1     AAPL                                          Apple Inc   147.280   
2     ABBV                                         Abbvie Inc   169.430   
3      ABC                           Amerisource Bergen Corp.   167.850   
4     ABMD                                       Abiomed Inc.   392.950   
5      ABT                                Abbott Laboratories   110.250   
6      ACN                            Accenture plc - Class A   300.435   
7     ADBE                                          Adobe Inc   337.970   
8      ADI                                Analog Devices Inc.   175.700   
9      ADM                         Archer Daniels Midland Co.    97.400   
10     ADP                     Automatic Data Processing Inc.   271.375   
11    ADSK                                      Autodesk Inc.   202.750   
12     AEE                                       Ameren Corp.    90.980   
13     AEP               American Electric Power Company Inc.   101.900   
14     AES                                          AES Corp.    30.040   
15     AFL                                         Aflac Inc.    70.090   
16     AIG                   American International Group Inc    64.050   
17     AIV    Apartment Investment & Management Co. - Class A     8.448   
18     AIZ                                       Assurant Inc   132.520   
19     AJG                          Arthur J. Gallagher & Co.   200.616   
20    AKAM                            Akamai Technologies Inc    92.770   
21     ALB                                    Albemarle Corp.   259.984   
22    ALGN                             Align Technology, Inc.   193.100   
23     ALK                              Alaska Air Group Inc.    46.020   
24     ALL                                Allstate Corp (The)   135.660   
25    ALLE                                       Allegion plc   111.850   
26    ALXN                       Alexion Pharmaceuticals Inc.   187.800   
27    AMAT                             Applied Materials Inc.   114.480   
28    AMCR                                          Amcor Plc    13.130   
29     AMD                        Advanced Micro Devices Inc.    73.230   
30     AME                                         Ametek Inc   142.848   
31    AMGN                                         AMGEN Inc.   290.665   
32     AMP                           Ameriprise Financial Inc   324.307   
33     AMT                               American Tower Corp.   216.865   
34    AMZN                                    Amazon.com Inc.    92.440   
35    ANET                                Arista Networks Inc   133.180   
36    ANSS                     Ansys Inc. - Registered Shares   254.330   
37    ANTM                                         Anthem Inc   497.530   
38     AON                                 Aon plc. - Class A   321.883   
39     AOS                                   A.O. Smith Corp.    60.820   
40     APA                                    APA Corporation    43.560   
41     APD                      Air Products & Chemicals Inc.   321.841   
42     APH                           Amphenol Corp. - Class A    82.150   
43    APTV                                          Aptiv PLC    93.120   
44     ARE               Alexandria Real Estate Equities Inc.   152.210   
45     ATO                                 Atmos Energy Corp.   122.360   
46    ATVI                            Activision Blizzard Inc    76.009   
47     AVB                         Avalonbay Communities Inc.   172.180   
48    AVGO                                       Broadcom Inc   550.100   
49     AVY                               Avery Dennison Corp.   180.800   
50     AWK                      American Water Works Co. Inc.   157.547   
51     AXP                               American Express Co.   158.860   
52     AZO                   

# Calculating Value Percentiles
Metrics:

 1. price to earnings ratio
 2. price to book ratio
 3. price to sales ratio
 4. EV/EBITDA
 5. EV/GP

In [37]:
from scipy.stats import percentileofscore as score

metrics = {
    'Price-to-Earnings Ratio': 'PE Percentile',
    'Price-to-Book Ratio' : 'PB Percentile',
    'Price-to-Sales Ratio': 'PS Percentile',
    'EV/EBITDA': 'EV/EBITDA Percentile',
    'EV/GP' : 'EV/GP Percentile',
}

for metric in metrics.keys():
    for row in rv_dataframe.index:
        rv_dataframe.loc[row, metrics[metric]] = stats.percentileofscore(rv_dataframe[metric], rv_dataframe.loc[row, metric])

rv_dataframe

Ticker                                        companyName     Price  \
0      AAP                             Advance Auto Parts Inc   150.190   
1     AAPL                                          Apple Inc   147.280   
2     ABBV                                         Abbvie Inc   169.430   
3      ABC                           Amerisource Bergen Corp.   167.850   
4     ABMD                                       Abiomed Inc.   392.950   
5      ABT                                Abbott Laboratories   110.250   
6      ACN                            Accenture plc - Class A   300.435   
7     ADBE                                          Adobe Inc   337.970   
8      ADI                                Analog Devices Inc.   175.700   
9      ADM                         Archer Daniels Midland Co.    97.400   
10     ADP                     Automatic Data Processing Inc.   271.375   
11    ADSK                                      Autodesk Inc.   202.750   
12     AEE                                       Ameren Corp.    90.980   
13     AEP               American Electric Power Company Inc.   101.900   
14     AES                                          AES Corp.    30.040   
15     AFL                                         Aflac Inc.    70.090   
16     AIG                   American International Group Inc    64.050   
17     AIV    Apartment Investment & Management Co. - Class A     8.448   
18     AIZ                                       Assurant Inc   132.520   
19     AJG                          Arthur J. Gallagher & Co.   200.616   
20    AKAM                            Akamai Technologies Inc    92.770   
21     ALB                                    Albemarle Corp.   259.984   
22    ALGN                             Align Technology, Inc.   193.100   
23     ALK                              Alaska Air Group Inc.    46.020   
24     ALL                                Allstate Corp (The)   135.660   
25    ALLE                                       Allegion plc   111.850   
26    ALXN                       Alexion Pharmaceuticals Inc.   187.800   
27    AMAT                             Applied Materials Inc.   114.480   
28    AMCR                                          Amcor Plc    13.130   
29     AMD                        Advanced Micro Devices Inc.    73.230   
30     AME                                         Ametek Inc   142.848   
31    AMGN                                         AMGEN Inc.   290.665   
32     AMP                           Ameriprise Financial Inc   324.307   
33     AMT                               American Tower Corp.   216.865   
34    AMZN                                    Amazon.com Inc.    92.440   
35    ANET                                Arista Networks Inc   133.180   
36    ANSS                     Ansys Inc. - Registered Shares   254.330   
37    ANTM                                         Anthem Inc   497.530   
38     AON                                 Aon plc. - Class A   321.883   
39     AOS                                   A.O. Smith Corp.    60.820   
40     APA                                    APA Corporation    43.560   
41     APD                      Air Products & Chemicals Inc.   321.841   
42     APH                           Amphenol Corp. - Class A    82.150   
43    APTV                                          Aptiv PLC    93.120   
44     ARE               Alexandria Real Estate Equities Inc.   152.210   
45     ATO                                 Atmos Energy Corp.   122.360   
46    ATVI                            Activision Blizzard Inc    76.009   
47     AVB                         Avalonbay Communities Inc.   172.180   
48    AVGO                                       Broadcom Inc   550.100   
49     AVY                               Avery Dennison Corp.   180.800   
50     AWK                      American Water Works Co. Inc.   157.547   
51     AXP                               American Express Co.   158.860   
52     AZO                   

# Calculating RV Score

We'll now calculate our RV Score (Robust Value), which is the value score that we'll use to filter for stocks in this invest strategy. 

The RV Score will be the arithmetic mean of the 4 percentile scores that we calculated in the last section. 

To calculate arithmetic mean, we will use the mean function from Python's built-in statistics module. 

In [38]:
from statistics import mean

for row in rv_dataframe.index:
    pe_ratio = rv_dataframe.loc[row, 'PE Percentile']
    pb_ratio = rv_dataframe.loc[row, 'PB Percentile']
    ps_ratio = rv_dataframe.loc[row, 'PS Percentile']
    ev_to_ebitda = rv_dataframe.loc[row, 'EV/EBITDA Percentile']
    ev_to_gp = rv_dataframe.loc[row, 'EV/GP Percentile']
    rv_dataframe.loc[row, 'RV Score'] = round(mean([pe_ratio, pb_ratio, ps_ratio, ev_to_ebitda, ev_to_gp]))
    
rv_dataframe[['Ticker', 'PE Percentile', 'PB Percentile', 'PS Percentile', 'EV/EBITDA Percentile', 'EV/GP Percentile', 'RV Score']]

Ticker PE Percentile PB Percentile PS Percentile EV/EBITDA Percentile  \
0      AAP     38.353414     53.564257     12.751004            28.614458   
1     AAPL     57.429719     98.192771     83.584337            70.080321   
2     ABBV     50.401606     94.477912     78.915663             41.26506   
3      ABC     47.941767      0.803213       0.60241            32.128514   
4     ABMD     93.975904     89.859438     99.196787            98.995984   
5      ABT     59.638554     70.833333     74.046185            66.767068   
6      ACN     65.963855     84.236948     57.630522            64.457831   
7     ADBE     76.807229      88.75502     91.666667            86.746988   
8      ADI     76.706827     40.913655     87.851406            79.919679   
9      ADM     26.305221     33.283133      6.425703            28.714859   
10     ADP     81.927711     97.791165     85.391566            90.361446   
11    ADSK     94.277108     98.594378     89.407631            97.791165   
12     AEE     51.305221     37.198795     55.773092                 50.0   
13     AEP     46.285141      32.53012     50.150602            40.461847   
14     AES      1.405622     81.124498     28.162651            36.546185   
15     AFL     15.662651     27.208835     39.859438            15.361446   
16     AIG      5.572289     14.909639     12.048193             1.907631   
17     AIV      6.526104     21.736948      85.64257            90.060241   
18     AIZ      53.11245     22.891566     10.240964             9.638554   
19     AJG     84.136546     67.018072     78.313253            81.827309   
20    AKAM     68.875502     56.325301     71.736948            78.915663   
21     ALB     44.678715      65.61245       81.2249            43.373494   
22    ALGN     70.783133      61.24498     70.883534             60.64257   
23     ALK     97.289157     18.624498      8.534137             8.935743   
24     ALL      1.104418      36.24498     10.140562            10.240964   
25    ALLE     53.714859     90.963855     58.433735            72.188755   
26    ALXN     93.574297     42.319277     63.905622            55.973896   
27    AMAT     32.078313     81.927711     68.072289            37.449799   
28    AMCR     51.706827     67.018072     22.690763            39.558233   
29     AMD     88.554217     32.228916     78.162651            84.839357   
30     AME     69.678715     65.411647     80.471888            76.405622   
31    AMGN     52.108434     97.690763     83.032129            50.702811   
32     AMP     28.514056     88.253012     44.628514            26.807229   
33     AMT     79.317269     93.273092     93.674699             83.73494   
34    AMZN     95.682731      78.76506     31.927711            71.787149   
35    ANET       81.2249     85.542169     94.879518             91.26506   
36    ANSS      89.35743      66.86747     95.481928             94.97992   
37    ANTM     44.829317     54.919679     12.449799            51.907631   
38     AON     55.271084     42.319277     63.905622            55.973896   
39     AOS     41.064257     62.951807     36.295181            29.819277   
40     APA      5.823293     95.682731     23.443775             2.108434   
41     APD     74.046185     73.544177      82.53012            68.373494   
42     APH     65.461847     80.923695     69.126506            67.269076   
43    APTV     95.883534     52.811245     26.355422            91.164659   
44     ARE     89.156627     16.516064     94.678715            83.333333   
45     ATO     49.598394     25.502008     73.293173            69.076305   
46    ATVI     78.815261     54.919679      88.75502            88.453815   
47     AVB     43.072289     34.086345     93.423695            79.417671   
48    AVGO     57.730924     87.751004     86.094378            52.108434   
49     AVY     40.662651     80.321285     28.463855            40.863454   
50     AWK     50.200803     58.684739     87.550201            85.040161   


# Selecting the 10th best value stocks

In [ ]:
rv_dataframe.sort_values('RV Score', ascending=True, inplace=True)
rv_dataframe.reset_index(drop=True, inplace=True)
rv_dataframe.head(10)


# Formatting our excel output

In [39]:
writer = pd.ExcelWriter('value_strategy2.xlsx', engine = 'xlsxwriter')
rv_dataframe.to_excel(writer, sheet_name='Value Strategy', index=False)


In [ ]:
background_color = '#0a0a23'
background_data_color = '#ffffff'
font_color = '#ffffff'
font_data_color = '#000000'

string_template = writer.book.add_format(
        {
            'font_color': font_color,
            'bg_color': background_color,
            'border': 1
        }
    )

dollar_template = writer.book.add_format(
        {
            'num_format':'$0.00',
            'font_color': font_color,
            'bg_color': background_color,
            'border': 1
        }
    )

integer_template = writer.book.add_format(
        {
            'num_format':'0',
            'font_color': font_color,
            'bg_color': background_color,
            'border': 1
        }
    )

float_template = writer.book.add_format(
        {
            'num_format':'0',
            'font_color': font_color,
            'bg_color': background_color,
            'border': 1
        }
    )

percent_template = writer.book.add_format(
        {
            'num_format':'0.0%',
            'font_color': font_color,
            'bg_color': background_color,
            'border': 1
        }
    )

In [ ]:
column_formats = {
                    'A': ['Ticker', string_template],
                    'B': ['Price', dollar_template],
                    'C': ['Number of Shares to Buy', integer_template],
                    'D': ['Price-to-Earnings Ratio', float_template],
                    'E': ['PE Percentile', percent_template],
                    'F': ['Price-to-Book Ratio', float_template],
                    'G': ['PB Percentile',percent_template],
                    'H': ['Price-to-Sales Ratio', float_template],
                    'I': ['PS Percentile', percent_template],
                    'J': ['EV/EBITDA', float_template],
                    'K': ['EV/EBITDA Percentile', percent_template],
                    'L': ['EV/GP', float_template],
                    'M': ['EV/GP Percentile', percent_template],
                    'N': ['RV Score', percent_template]
                 }

for column in column_formats.keys():
    writer.sheets['Value Strategy'].set_column(f'{column}:{column}', 25, column_formats[column][1])
    writer.sheets['Value Strategy'].write(f'{column}1', column_formats[column][0], column_formats[column][1])

In [ ]:
writer.save()